In [1]:
import random
import matplotlib.pyplot as plt
import numpy as np
from math import radians, degrees
from scipy.optimize import minimize
import cirq
from cirq_web import bloch_sphere

def binary_labels(num_qubits):
    return [bin(x)[2:].zfill(num_qubits) for x in range (2**num_qubits)]

plt.rcParams.update({'font.size': 8})

# Part 1: Rotation Gates

#### 1.1: Creating a circuit that applies a 180 degree rotation around the X-axis to a single qubit and visualize in Bloch Sphere

- The `cirq.rx` gate represents a rotation around the X-axis of the Bloch sphere. The rotation angle is given in radians.

- `radians(180)` converts 180 degrees to radians, which equals $\pi$ radians. This corresponds to a 180-degree rotation around the X-axis.

- The `.on(qubit)` method applies this rotation to the qubit `q0`.
- The `cirq.final_state_vector(circuit)` function calculates the qubit's final state vector. `bloch_sphere.BlochSphere` is a hypothetical function for visualizing this state on the Bloch sphere, possibly a custom tool or placeholder not in Cirq.



In [2]:
qubit = cirq.NamedQubit('q0')
circuit = cirq.Circuit()

circuit.append(cirq.rx(radians(180)).on(qubit))

bloch_sphere.BlochSphere(state_vector=cirq.final_state_vector(circuit))

#### 1.2: Creating a circuit that applies a 45 degree rotation around the X-axis to a single qubit and visualize in Bloch Sphere

In [3]:
qubit = cirq.NamedQubit('q0')
circuit = cirq.Circuit()

circuit.append(cirq.rx(radians(45)).on(qubit))

bloch_sphere.BlochSphere(state_vector=cirq.final_state_vector(circuit))

#### 1.3: Creating a circuit that appliesan H-Gate then a 90 degree rotation around the X-axis to a single qubit and visualize.

In [4]:
qubit = cirq.NamedQubit('q0')
circuit = cirq.Circuit()

circuit.append(cirq.H(qubit))
circuit.append(cirq.rz(radians(90)).on(qubit))

bloch_sphere.BlochSphere(state_vector=cirq.final_state_vector(circuit))

#### 1.4: Creating a circuit that applies a 400 degree rotation around the X-axis to a single qubit and visualize in Bloch Sphere

In [5]:
qubit = cirq.NamedQubit('q0')
circuit = cirq.Circuit()

circuit.append(cirq.rx(radians(400)).on(qubit))

bloch_sphere.BlochSphere(state_vector=cirq.final_state_vector(circuit))

# Part 2: Implementing Variational Algorithm 

## **Part 2.1: The Cost Function and Expectation Value**

Before implementing the full variational algorithm, it is crucial to understand how to define a cost function and compute its expectation value based on the measurements from the quantum circuit.

A **cost function** is a mathematical function that quantifies the error or deviation of a solution from the desired outcome. In the context of variational algorithms, the cost function is an observable whose expectation value is minimized or maximized to solve a specific problem. The parameters of the quantum circuit are adjusted to optimize this cost function.

#### **Implementing the Cost Function in 4 Steps:**

1. **Create a Circuit Ansatz:**
   - An ansatz is a parameterized quantum circuit that prepares a trial wave function or state. The circuit is designed to be flexible, allowing parameters to be adjusted to minimize or optimize the cost function.
   - Typically, the ansatz consists of a series of quantum gates with variable parameters. These parameters are adjusted during the optimization process.
   - The choice of ansatz can significantly impact the performance of the variational algorithm, as it determines the expressiveness and complexity of the states that can be represented.

2. **Simulate the Circuit and Unpack the Result:**
   - Once the ansatz is constructed, it is simulated to obtain the quantum state after applying all the gates.
   - The simulation can be done using a quantum simulator or a real quantum device. The output of this simulation is usually a set of measurement results or a state vector.
   - If using a simulator, you can directly obtain the final state vector. On a real device, repeated measurements will provide the probabilities of different outcomes.

3. **Calculate the Average (Expected) State:**
   - The average or expected state is determined from the measurement results. This involves computing the probabilities or expectation values of observables related to the quantum state.
   - The expectation value is calculated using the formula:
     $$ \langle O \rangle = \sum_i p_i \langle \psi_i | O | \psi_i \rangle $$
     where $p_i$ is the probability of the $i$-th state, and $O$ is the observable.

4. **Calculate the Average (Expected) Cost:**
   - The cost function is defined based on the problem you are trying to solve. It is usually an observable whose expectation value you wish to minimize or maximize.
   - The average cost is calculated as the expectation value of the cost function using the results from the previous step.
   - The calculated cost guides the optimization process, where the parameters of the ansatz are adjusted to minimize the cost function.

By following these steps, you can implement a cost function for a variational algorithm and compute its expectation value, which is crucial for optimizing the algorithm's parameters.


#### Step 2.1.1 : Create a circuit anstaz.
- Starting with a simple circuit : Preparing $|1\rangle$ state

**Note :** To make the measurement result easier, we should name the collection of measurement using the key parameter.
- Specifically, srtting key = `result`


In [6]:
qubit = cirq.NamedQubit('q0')
circuit = cirq.Circuit()

circuit.append(cirq.X(qubit))
circuit.append(cirq.measure(qubit, key='result'))

circuit

q0: ───X───M('result')───

#### Step 2.1.2: Simulate the Circuit and Unpack the Result
- Accessing the specific states measured using the key (result) we assigned above.

In [7]:
sim = cirq.Simulator()

results = sim.run(circuit, repetitions=100)

measurements = results.measurements['result']

#### Step 2.1.3: Calculate the Average (Expected) State

- `np.mean(measurements, axis=0)` computes the average of measurement outcomes along each column of the `measurements` array. This provides the average result for each observable or qubit across all experiments. Here, `axis=0` specifies that the mean is calculated down each column.



In [8]:
average_state = np.mean(measurements, axis=0)
average_state    

array([1.])

#### Step 2.1.4 : Define a Cost Function and Calculate the Average (Expected) Cost

- For Example:  $Average Cost = Average State * 2$

**Note :** Here we can define any cost function we want, Like:
- $Average Cost = Average State * 10$
- $Average Cost = 1 - Average State$

....etc

In [9]:
average_cost = average_state[0]*2

average_cost

2.0

### Question: Implement the 4-step and find cost where:
- Initial state is $|+\rangle$
- circuit that rotates the qubit around X-axis by 45 degree
- $Average Cost = 1 - Average State$

In [10]:
# Solve

# Creating a circuit anstaz
qubit = cirq.NamedQubit('q0')
circuit = cirq.Circuit()

circuit.append(cirq.H(qubit))
circuit.append(cirq.rx(radians(45)).on(qubit))
circuit.append(cirq.measure(qubit, key='result'))

print('Circuit :',circuit)

# Simulating the Circuit and Unpack the Result
sim = cirq.Simulator()
results = sim.run(circuit, repetitions=100)
measurements = results.measurements['result']


# Calculateing the Average (Expected) State
average_state = np.mean(measurements, axis=0)
print('\nAverage State :',average_state)

 
# Defining a Cost Function and Calculating the Average (Expected) Cost
average_cost = 1 - average_state[0]
print('\nAverage Cost :', average_cost)

Circuit : q0: ───H───Rx(0.25π)───M('result')───

Average State : [0.57]

Average Cost : 0.43000000000000005


## **Part 2.2: The Full Algorithm**

Let's put everything together to implement the full variational algorithm.

#### Let's Optimize Using SciPy's `minimize(...)` Function in 3 Steps

1. **Define the Average Cost Function Ansatz:**
   - The cost function ansatz is a parameterized function that represents the cost associated with a given quantum state. 
   - It involves constructing a quantum circuit with adjustable parameters and defining an observable to measure.
   - The expectation value of this observable, calculated from the circuit's output state, forms the cost that needs to be minimized.

2. **Define an Initial Guess State:**
   - An initial guess for the parameter values of the ansatz is needed to start the optimization process.
   - This initial guess can be randomly generated or based on some prior knowledge of the problem.
   - The choice of the initial guess can affect the convergence and performance of the optimization algorithm.

3. **Provide the Average Cost Function Ansatz and Initial Guess to the `minimize(...)` Function:**
   - Use SciPy's `minimize` function to find the parameter values that minimize the cost function.
   - The `minimize` function takes the cost function ansatz, initial parameter guess, and optimization method as input arguments.
   - It iteratively adjusts the parameters to find the minimum cost, effectively optimizing the quantum circuit to approximate the desired solution.

By following these steps, we can implement the full variational algorithm to optimize the quantum circuit parameters, aiming to minimize the defined cost function and solve a given problem efficiently.


#### Step 2.2.1: Define the Average Cost Function Ansatz
- By using previous code creating `average_cost` function.
- It create circuit that rotates a single qubit around the X-axis by the given `angle`
- Finally it returns the cost


In [11]:
def average_cost(angle):

    # Creating a circuit anstaz
    qubit = cirq.NamedQubit('q0')
    circuit = cirq.Circuit()

    circuit.append(cirq.rx(radians(angle)).on(qubit))
    circuit.append(cirq.measure(qubit, key='result'))

    # Simulating the Circuit and Unpack the Result
    sim = cirq.Simulator()
    results = sim.run(circuit, repetitions=2000)
    measurements = results.measurements['result']


    # Calculateing the Average (Expected) State
    average_state = np.mean(measurements, axis=0)

    
    # Defining a Cost Function and Calculating the Average (Expected) Cost
    average_cost = 1 - average_state[0]
    
    print('Attempt: ', angle, ' Produces Average Cost: ', average_cost)
    
    return average_cost

#### Step 2.2.2: Define an Initial Guess State
- Here we are picking the initial angle (in degrees) that the `minimize()` function will then optimize.
- Picking the best initial guess is a mix of art and science. let's pick 90 degrees since that will produce an equal superposition of $|0\rangle$ and $|1\rangle$ 

In [12]:
initial_guess = 90

#### Step 2.2.3: Provide the Average Cost Function Ansatz and Initial Guess to the `minimize(...)` Function

**Note :** A trademark of variational and optimization algorithms is that we may get different results each time.
- For Example: Here we may need to run the code to get close to the correct answer (A cost function of 0 at 180 degrees in this case)

**Two Important Function:**

- **`minimize(average_cost, initial_guess, method='Powell')`:**
   - This function call is part of the SciPy library's optimization module. It is used to find the minimum of the scalar function `average_cost`.
   - **`average_cost`**: The function to be minimized. It takes a parameter (the angle) and returns a scalar value representing the cost for that angle.
   - **`initial_guess`**: The starting point for the optimization algorithm. This is an initial estimate of the angle that might minimize the cost function. It is provided as a list or array.
   - **`method='Powell'`**: Specifies the optimization algorithm to be used. Powell's method is a derivative-free optimization algorithm, which is useful for functions that are not smooth or do not have derivatives.

- **`print('\nOptimized Angle(s) in Degrees: ', [a % 360 for a in result.x])`:**
   - This line outputs the optimized angles to the console.
   - **`result.x`**: After the `minimize` function is executed, `result` contains the optimization result, with `result.x` holding the optimal values of the parameters (the angle(s)).
   - **`[a % 360 for a in result.x]`**: This list comprehension converts each optimized angle in `result.x` to a value between 0 and 360 degrees. The modulo operation `% 360` ensures that the angle falls within the typical range for angles in degrees.
   - The `print` statement outputs a message showing the optimized angle(s) in degrees. The `\n` at the beginning of the string is a newline character, which moves the output to a new line for better readability.

In [13]:
result = minimize(average_cost, initial_guess, method='Powell')

# Output the optimized parameter 
print('\nOptimized Angle(For which Average Cost = 0) in Degrees: ', [a%360 for a in result.x])

# Output the state on a Bloch Sphere 
qubit = cirq.NamedQubit('q0')
circuit = cirq.Circuit()

circuit.append(cirq.rx(radians(result.x[0])).on(qubit))

bloch_sphere.BlochSphere(state_vector=cirq.final_state_vector(circuit))

Attempt:  [90.]  Produces Average Cost:  0.481
Attempt:  [90.]  Produces Average Cost:  0.5085
Attempt:  [91.]  Produces Average Cost:  0.49150000000000005
Attempt:  [92.618034]  Produces Average Cost:  0.474
Attempt:  [94.09829087]  Produces Average Cost:  0.4595
Attempt:  [96.4933968]  Produces Average Cost:  0.43700000000000006
Attempt:  [140.63973249]  Produces Average Cost:  0.12350000000000005
Attempt:  [212.0700046]  Produces Average Cost:  0.07750000000000001
Attempt:  [182.11799243]  Produces Average Cost:  0.0004999999999999449
Attempt:  [166.27470739]  Produces Average Cost:  0.015000000000000013
Attempt:  [193.55864271]  Produces Average Cost:  0.014000000000000012
Attempt:  [180.15531381]  Produces Average Cost:  0.0
Attempt:  [179.25376067]  Produces Average Cost:  0.0
Attempt:  [178.36122306]  Produces Average Cost:  0.0
Attempt:  [173.74458502]  Produces Average Cost:  0.0034999999999999476
Attempt:  [176.5978243]  Produces Average Cost:  0.0004999999999999449
Attempt: 

### Implementation of the Full Variational Algorithm

This code snippet demonstrates the implementation of a variational algorithm using a simple quantum circuit with a single qubit. The goal is to optimize the rotation angle to minimize a defined cost function.

#### **Function Definition: $average\_cost(angle)$**

1. **Create a Circuit Ansatz:**
   - We define a single-qubit circuit using Cirq.
   - The circuit applies a rotation around the X-axis ($rx$) by an angle (in radians) to the qubit $q0$.
   - The qubit is then measured, with results stored under the key $'result'$.

2. **Simulate the Circuit and Unpack the Result:**
   - We use Cirq's $Simulator$ to run the circuit for 100 repetitions.
   - The measurement outcomes are stored in the $measurements$ array.

3. **Calculate the Average (Expected) State:**
   - The average state is calculated as the mean of the measurement outcomes.
   - This average represents the probability of measuring the qubit in the $|1\rangle$ state.

4. **Define the Cost Function and Calculate the Average (Expected) Cost:**
   - The cost function is defined as $1 - average\_state[0]$, aiming to maximize the probability of measuring the qubit in the $|0\rangle$ state.
   - This value is returned as the cost for a given angle.

#### **Optimization Process**

- We define an initial guess for the angle as $90$ degrees.
- SciPy's $minimize$ function is used to optimize the angle, minimizing the $average\_cost$ function.
- The $Powell$ method is chosen for optimization.

#### **Output**

- The optimized angle(s) are printed, ensuring they are within a range of $0$ to $360$ degrees.
- A final circuit is constructed with the optimized angle, and its state is visualized on a Bloch Sphere using a hypothetical $bloch\_sphere.BlochSphere$ function.
- Here, we may need to run the code multiple times to get close to the correct answer (a cost function of 0 at 180 degrees in this case). This repetition ensures convergence to the optimal solution due to the stochastic nature of quantum measurements.

### Question 1: Implement the Full Variational Algorithm :

- Use an Ansatz circuit with a rotational Z-Gate.
- Define the Cost Function as $(\text{State} - 0.5)^2$.


In [14]:
# 1. Defining the Average Cost Function Ansatz
def average_cost(angle):

    # Creating a circuit anstaz
    qubit = cirq.NamedQubit('q0')
    circuit = cirq.Circuit()

    circuit.append(cirq.rz(radians(angle)).on(qubit))                       # change here!!!
    circuit.append(cirq.measure(qubit, key='result'))

    # Simulating the Circuit and Unpack the Result
    sim = cirq.Simulator()
    results = sim.run(circuit, repetitions=2000)
    measurements = results.measurements['result']


    # Calculateing the Average (Expected) State
    average_state = np.mean(measurements, axis=0)

    
    # Defining a Cost Function and Calculating the Average (Expected) Cost
    average_cost = (average_state[0] - 0.5)**2                              # change here!!!
    
    print('Attempt: ', angle, ' Produces Average Cost: ', average_cost)
    
    return average_cost




# 2. Defining an Initial Guess State
initial_guess = 90                                            # changed here!!! (not necessary 90 is a good guess for here)





# 3. Providing the Average Cost Function Ansatz and Initial Guess to the `minimize(...)` Function
result = minimize(average_cost, initial_guess, method='Powell')

# Output the optimized parameter 
print('\nOptimized Angle(For which Average Cost = 0) in Degrees: ', [a%360 for a in result.x])

# Output the state on a Bloch Sphere 
qubit = cirq.NamedQubit('q0')
circuit = cirq.Circuit()

circuit.append(cirq.rx(radians(result.x[0])).on(qubit))

bloch_sphere.BlochSphere(state_vector=cirq.final_state_vector(circuit))

Attempt:  [90.]  Produces Average Cost:  0.25
Attempt:  [90.]  Produces Average Cost:  0.25
Attempt:  [91.]  Produces Average Cost:  0.25
Attempt:  [92.618034]  Produces Average Cost:  0.25
Attempt:  [91.61803397]  Produces Average Cost:  0.25
Attempt:  [91.99999998]  Produces Average Cost:  0.25
Attempt:  [92.23606797]  Produces Average Cost:  0.25
Attempt:  [92.381966]  Produces Average Cost:  0.25
Attempt:  [92.47213595]  Produces Average Cost:  0.25
Attempt:  [92.52786405]  Produces Average Cost:  0.25
Attempt:  [92.5623059]  Produces Average Cost:  0.25
Attempt:  [92.58792896]  Produces Average Cost:  0.25

Optimized Angle(For which Average Cost = 0) in Degrees:  [92.58792896154584]


### Question 2: Implement the Full Variational Algorithm :

- Use an Ansatz circuit with a rotational Y-Gate.
- Define the Cost Function as $(\text{State} - 0.75)^2$.

**Note :** In this case we are looking for an angle that is a 75% rotation around the Y-axis, meaning the ideal parameter value(angle) is close to either 135 or 225 degrees

In [15]:
# 1. Defining the Average Cost Function Ansatz
def average_cost(angle):

    # Creating a circuit anstaz
    qubit = cirq.NamedQubit('q0')
    circuit = cirq.Circuit()

    circuit.append(cirq.ry(radians(angle)).on(qubit))                       # change here!!!
    circuit.append(cirq.measure(qubit, key='result'))

    # Simulating the Circuit and Unpack the Result
    sim = cirq.Simulator()
    results = sim.run(circuit, repetitions=2000)
    measurements = results.measurements['result']


    # Calculateing the Average (Expected) State
    average_state = np.mean(measurements, axis=0)

    
    # Defining a Cost Function and Calculating the Average (Expected) Cost
    average_cost = (average_state[0] - 0.75)**2                              # change here!!!
    
    print('Attempt: ', angle, ' Produces Average Cost: ', average_cost)
    
    return average_cost




# 2. Defining an Initial Guess State
initial_guess = 0                                            # changed here!!! (choose any)





# 3. Providing the Average Cost Function Ansatz and Initial Guess to the `minimize(...)` Function
result = minimize(average_cost, initial_guess, method='Powell')

# Output the optimized parameter 
print('\nOptimized Angle(For which Average Cost = 0) in Degrees: ', [a%360 for a in result.x])

# Output the state on a Bloch Sphere 
qubit = cirq.NamedQubit('q0')
circuit = cirq.Circuit()

circuit.append(cirq.rx(radians(result.x[0])).on(qubit))

bloch_sphere.BlochSphere(state_vector=cirq.final_state_vector(circuit))

Attempt:  [0.]  Produces Average Cost:  0.5625
Attempt:  [0.]  Produces Average Cost:  0.5625
Attempt:  [1.]  Produces Average Cost:  0.5625
Attempt:  [2.618034]  Produces Average Cost:  0.5625
Attempt:  [1.61803397]  Produces Average Cost:  0.561001
Attempt:  [1.99999998]  Produces Average Cost:  0.5625
Attempt:  [1.49999999]  Produces Average Cost:  0.5625
Attempt:  [1.74999999]  Produces Average Cost:  0.5625
Attempt:  [1.63421431]  Produces Average Cost:  0.5625
Attempt:  [1.57294901]  Produces Average Cost:  0.5617502500000001
Attempt:  [1.60185364]  Produces Average Cost:  0.5625
Attempt:  [3.23606795]  Produces Average Cost:  0.559504
Attempt:  [1.61803397]  Produces Average Cost:  0.5625
Attempt:  [3.23606795]  Produces Average Cost:  0.5625
Attempt:  [5.85410193]  Produces Average Cost:  0.558009
Attempt:  [10.09016993]  Produces Average Cost:  0.5527922500000001
Attempt:  [16.69382261]  Produces Average Cost:  0.537289
Attempt:  [27.37875716]  Produces Average Cost:  0.481635